In [39]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import spacy
import en_core_web_md
import csv
import regex as re
import os
import spacy
from gensim.models import LdaModel
from gensim.corpora.dictionary import Dictionary
from gensim.models import LdaMulticore
from gensim.models import CoherenceModel
from gensim import corpora
from pprint import pprint

In [2]:
path = './DataUCSB/'
list_of_files = []

for root, dirs, files in os.walk(path):
    for file in files:
        list_of_files.append(os.path.join(root,file))

len(list_of_files)

135

In [3]:
filepath = './DataUCSB/address-before-joint-session-the-congress-the-state-the-union-16.csv'
speeches = []
for file in list_of_files:
    with open(filepath, 'r') as read_obj: # read csv file as a list of lists
      csv_reader = csv.reader(read_obj) # pass the file object to reader() to get the reader object
      speechList = sum(list(csv_reader), []) # Pass reader object to list() to get a list of lists (matrix)
                                            # sum(list, []) flattens 2D matrix into a vector
      speech = ''.join(speechList)
    speeches.append(speech)

<A HREF="https://regexr.com/">RegExr regex tester</A>

In [8]:
#Load SpaCy English Model
nlp = en_core_web_md.load()

#Tags to remove
extags = ['PRON','CCONJ','PUNCT','PART','DET','ADP','NUM','SYM','SPACE']

tokens=[]
#SpaCy tokenization + lemmatization + lowercase
for speech in nlp.pipe(speeches):
    scr_tok = [token.lemma_.lower() for token in speech if token.pos_ not in extags and not token.is_stop and token.is_alpha]
    tokens.append(scr_tok)


In [32]:
#Tags to remove
extags = ['PRON','CCONJ','PUNCT','PART','DET','ADP','NUM','SYM','SPACE']
# creates list of objects (not strings)
tokens_obj = [ (token.lower() for token in speech  if token.isalpha() and not token.is_stop) for speech in speeches]
#tokens_obj = [ (token.lemma_.lower() for token in speech if token.pos_ not in extags and not token.is_stop and token.is_alpha) for speech in speeches ]


In [33]:
dictionary = Dictionary(tokens)

In [34]:

#dictionary.filter_extremes(no_below=10, no_above=0.5)
#Convert token counts into bag of words (BoW) corpus
corpus = [dictionary.doc2bow(token) for token in tokens]

In [35]:
corpus

[[(0, 1),
  (1, 4),
  (2, 3),
  (3, 2),
  (4, 1),
  (5, 2),
  (6, 1),
  (7, 2),
  (8, 2),
  (9, 3),
  (10, 2),
  (11, 1),
  (12, 1),
  (13, 1),
  (14, 1),
  (15, 2),
  (16, 3),
  (17, 6),
  (18, 1),
  (19, 1),
  (20, 4),
  (21, 2),
  (22, 6),
  (23, 3),
  (24, 5),
  (25, 2),
  (26, 1),
  (27, 1),
  (28, 1),
  (29, 4),
  (30, 1),
  (31, 1),
  (32, 1),
  (33, 3),
  (34, 2),
  (35, 1),
  (36, 3),
  (37, 26),
  (38, 19),
  (39, 12),
  (40, 1),
  (41, 2),
  (42, 1),
  (43, 3),
  (44, 1),
  (45, 2),
  (46, 1),
  (47, 1),
  (48, 1),
  (49, 1),
  (50, 2),
  (51, 6),
  (52, 1),
  (53, 1),
  (54, 1),
  (55, 1),
  (56, 1),
  (57, 2),
  (58, 2),
  (59, 1),
  (60, 1),
  (61, 1),
  (62, 1),
  (63, 6),
  (64, 1),
  (65, 1),
  (66, 2),
  (67, 1),
  (68, 1),
  (69, 2),
  (70, 2),
  (71, 2),
  (72, 2),
  (73, 10),
  (74, 1),
  (75, 8),
  (76, 4),
  (77, 1),
  (78, 10),
  (79, 1),
  (80, 2),
  (81, 1),
  (82, 1),
  (83, 1),
  (84, 1),
  (85, 2),
  (86, 2),
  (87, 2),
  (88, 1),
  (89, 1),
  (90, 1),
  (9

In [47]:
# Make a index to word dictionary.

temp = dictionary[0]  # This is only to "load" the dictionary.
id2word = dictionary.id2token

#Train the topic model

model = LdaModel(corpus=corpus, id2word=id2word,iterations=400, num_topics=10)
top_topics = list(model.top_topics(corpus))
pprint(top_topics)

[([(0.01357551, 'year'),
   (0.01253069, 'people'),
   (0.011707847, 'new'),
   (0.010427244, 'job'),
   (0.009222038, 'america'),
   (0.009013701, 'work'),
   (0.007501253, 'good'),
   (0.007421098, 'need'),
   (0.007042605, 'come'),
   (0.006997524, 'government'),
   (0.0068798214, 'business'),
   (0.006644078, 'american'),
   (0.006202167, 'nation'),
   (0.0061030663, 'world'),
   (0.0060853655, 'want'),
   (0.0060080527, 'know'),
   (0.0057601794, 'school'),
   (0.005506521, 'tonight'),
   (0.0051415176, 'high'),
   (0.0050869905, 'country')],
  1.0000889005818406e-12),
 ([(0.014981244, 'year'),
   (0.013463006, 'new'),
   (0.009715463, 'work'),
   (0.008124367, 'know'),
   (0.007986426, 'people'),
   (0.007873747, 'job'),
   (0.007672455, 'world'),
   (0.0076016914, 'nation'),
   (0.006341941, 'future'),
   (0.0062509375, 'come'),
   (0.0062363883, 'country'),
   (0.0059399367, 'time'),
   (0.0058969297, 'company'),
   (0.005748593, 'tonight'),
   (0.005717169, 'good'),
   (0.0057

In [49]:
for idx in range(10):
    print("Topic #%s:" % idx, model.print_topic(idx, 7))
print("=" * 20)


Topic #0: 0.014*"year" + 0.013*"people" + 0.012*"new" + 0.010*"job" + 0.009*"america" + 0.009*"work" + 0.008*"good"
Topic #1: 0.015*"year" + 0.013*"new" + 0.010*"work" + 0.008*"know" + 0.008*"people" + 0.008*"job" + 0.008*"world"
Topic #2: 0.001*"new" + 0.001*"year" + 0.001*"job" + 0.001*"work" + 0.001*"people" + 0.001*"know" + 0.001*"nation"
Topic #3: 0.001*"new" + 0.001*"year" + 0.001*"job" + 0.001*"work" + 0.001*"good" + 0.001*"school" + 0.001*"people"
Topic #4: 0.001*"new" + 0.001*"year" + 0.001*"people" + 0.001*"america" + 0.001*"nation" + 0.001*"job" + 0.001*"come"
Topic #5: 0.012*"year" + 0.010*"job" + 0.010*"people" + 0.010*"new" + 0.008*"work" + 0.007*"tonight" + 0.007*"future"
Topic #6: 0.001*"job" + 0.001*"year" + 0.001*"people" + 0.001*"new" + 0.001*"nation" + 0.001*"school" + 0.001*"know"
Topic #7: 0.001*"new" + 0.001*"people" + 0.001*"year" + 0.001*"nation" + 0.001*"work" + 0.001*"job" + 0.001*"world"
Topic #8: 0.017*"new" + 0.015*"year" + 0.011*"job" + 0.009*"america" + 

[[(0, 1),
  (1, 4),
  (2, 3),
  (3, 2),
  (4, 1),
  (5, 2),
  (6, 1),
  (7, 2),
  (8, 2),
  (9, 3),
  (10, 2),
  (11, 1),
  (12, 1),
  (13, 1),
  (14, 1),
  (15, 2),
  (16, 3),
  (17, 6),
  (18, 1),
  (19, 1),
  (20, 4),
  (21, 2),
  (22, 6),
  (23, 3),
  (24, 5),
  (25, 2),
  (26, 1),
  (27, 1),
  (28, 1),
  (29, 4),
  (30, 1),
  (31, 1),
  (32, 1),
  (33, 3),
  (34, 2),
  (35, 1),
  (36, 3),
  (37, 26),
  (38, 19),
  (39, 12),
  (40, 1),
  (41, 2),
  (42, 1),
  (43, 3),
  (44, 1),
  (45, 2),
  (46, 1),
  (47, 1),
  (48, 1),
  (49, 1),
  (50, 2),
  (51, 6),
  (52, 1),
  (53, 1),
  (54, 1),
  (55, 1),
  (56, 1),
  (57, 2),
  (58, 2),
  (59, 1),
  (60, 1),
  (61, 1),
  (62, 1),
  (63, 6),
  (64, 1),
  (65, 1),
  (66, 2),
  (67, 1),
  (68, 1),
  (69, 2),
  (70, 2),
  (71, 2),
  (72, 2),
  (73, 10),
  (74, 1),
  (75, 8),
  (76, 4),
  (77, 1),
  (78, 10),
  (79, 1),
  (80, 2),
  (81, 1),
  (82, 1),
  (83, 1),
  (84, 1),
  (85, 2),
  (86, 2),
  (87, 2),
  (88, 1),
  (89, 1),
  (90, 1),
  (9